# Hypothesis:

Stores closer to busstops have more revenue.

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import geopy.distance

from numba import jit, njit

In [2]:
stores_train = pd.read_csv('../data/stores_train.csv')

stores_test = pd.read_csv('../data/stores_test.csv')

busstops_norway =  pd.read_csv('../data/busstops_norway.csv')

In [3]:
stores_train_lon = stores_train["lon"].values
stores_train_lat = stores_train["lat"].values

stores_test_lon = stores_test["lon"].values
stores_test_lat = stores_test["lat"].values

busstops = busstops_norway["geometry"].values

busstops_lon = []
busstops_lat = []
for busstop in busstops:
    busstop = busstop.split("(")
    busstop = busstop[1].split(" ")
    busstop[1] = busstop[1].replace(")", "")
    busstops_lon.append(float(busstop[0]))
    busstops_lat.append(float(busstop[1]))
busstops_lon = np.asarray(busstops_lon)
busstops_lat = np.asarray(busstops_lat)

In [4]:
@njit
def distance_busstop_and_store(coo_busstop, coo_store):

    R = 6371000.0

    lat1 = np.deg2rad(coo_busstop[0])
    lon1 = np.deg2rad(coo_busstop[1])
    lat2 = np.deg2rad(coo_store[0])
    lon2 = np.deg2rad(coo_store[1])

    dlon = lon2 - lon1
    dlat = lat2 - lat1

    a = np.sin(dlat / 2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2)**2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1 - a))

    distance = R*c
    return distance

@njit
def find_closest_distance(stores_coo, busstops_coo,empty_array):
    closest_distances = empty_array
    for i in range(len(stores_coo[0])):
        print(i)
        coo_store = [stores_coo[0][i], stores_coo[1][i]]
        closest_distance = np.inf
        for j in range(len(busstops_coo[0])):
            busstop = [busstops_coo[0][j],busstops_coo[1][j]]
            distance = (distance_busstop_and_store(busstop, coo_store))
            if distance < closest_distance:
                closest_distance = distance
                #print(closest_distance)
                #print(coo_store)
                #print(busstop)
        closest_distances = np.append(closest_distances,closest_distance)          
    return closest_distances

#distances = find_closest_distance([stores_train_lon, stores_train_lat])
#print(distance_busstop_and_store([48.8566,2.3522],[50.0647,19.9450])) #Distance between Paris and Krakow
#print(distance_busstop_and_store([10.204927885979, 59.743104058362704],[6.54064723379766, 61.0618887850553])) #Got 430497

#10 stores in 2 min
#10/2 * 13000 = 43.33 hours runtime



In [5]:
epmty_array = np.array([])
distances = find_closest_distance([stores_train_lon, stores_train_lat],[busstops_lon, busstops_lat],epmty_array)

c:\Python310\lib\site-packages\numba\core\ir_utils.py:2147: NumbaPendingDeprecationWarning: 
Encountered the use of a type that is scheduled for deprecation: type 'reflected list' found for argument 'busstops_coo' of function 'find_closest_distance'.

For more information visit https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-reflection-for-list-and-set-types

File "..\..\..\..\..\..\..\..\..\AppData\Local\Temp\ipykernel_20660\3243582177.py", line 20:
<source missing, REPL/exec in use?>

  warnings.warn(NumbaPendingDeprecationWarning(msg, loc=loc))
c:\Python310\lib\site-packages\numba\core\ir_utils.py:2147: NumbaPendingDeprecationWarning: 
Encountered the use of a type that is scheduled for deprecation: type 'reflected list' found for argument 'stores_coo' of function 'find_closest_distance'.

For more information visit https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-reflection-for-list-and-set-types

File "..\..\..\..\..

0
[]
585.3544894172582
1
[585.35448942]
138.7983657767917
2
[585.35448942 138.79836578]
41.09951926046841
3
[585.35448942 138.79836578  41.09951926]
56.69301696189898
4
[585.35448942 138.79836578  41.09951926  56.69301696]
229.07795923765556
5
[585.35448942 138.79836578  41.09951926  56.69301696 229.07795924]
173.03702925075908
6
[585.35448942 138.79836578  41.09951926  56.69301696 229.07795924
 173.03702925]
196.12896418517462
7
[585.35448942 138.79836578  41.09951926  56.69301696 229.07795924
 173.03702925 196.12896419]
59.514878988332605
8
[585.35448942 138.79836578  41.09951926  56.69301696 229.07795924
 173.03702925 196.12896419  59.51487899]
272.48251619629923
9
[585.35448942 138.79836578  41.09951926  56.69301696 229.07795924
 173.03702925 196.12896419  59.51487899 272.4825162 ]
179.21690659141186
10
[585.35448942 138.79836578  41.09951926  56.69301696 229.07795924
 173.03702925 196.12896419  59.51487899 272.4825162  179.21690659]
192.71145322805933
11
[585.35448942 138.79836578

In [ ]:
print(distances)
feature = pd.DataFrame()
feature['distance_store_busstop'] = np.asarray(distances)

feature.to_csv('../features_csv/distance_store_busstop.csv', index = False)

[]
